# Recreate Gapminder

## Import libraries

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

## Load the data

In [ ]:
df = pd.read_csv('Gapminder-data.csv', sep=',')

In [ ]:
df.head()

In [ ]:
df.describe()

In [ ]:
df_info = pd.read_csv('Gapminder-info.csv', sep=',', index_col=0)

In [ ]:
df_info

Sort by size

In [ ]:
df = df.sort_values(['Year', 'Population'], ascending=[True, False])

## Create the bubble chart

In [ ]:
color_map = {
    'Asia': '#ff5872',
    'Americas': '#7feb00',
    'Africa': '#00d5e9',
    'Europe': '#ffe700'
}

In [ ]:
fig = px.scatter(
    df.query('Year==2020'),
    x='Income',
    y='Life expectancy',
    color='Region',
    size='Population',
    size_max=60,
    log_x=True,
    hover_name='Country',
    hover_data={c: False for c in df.columns},
    color_discrete_map=color_map,
    title='Gapminder<br><sup>Data from gapminder.org, CC-BY license</sup>'
)
fig.show()

In [ ]:
# Adjust markers
fig.update_traces(marker=dict(line=dict(color='black', width=0.8), opacity=0.9))
# Adjust figure layout
fig.update_layout(
    plot_bgcolor='white',
    font=dict(color='dimgray')
)
# Adjust axes and grid
fig.update_xaxes(
    linewidth=1,
    linecolor='dimgray',
    gridcolor='lightgray',
    showspikes=True,
    spikethickness=1,
    spikecolor='dimgray'
)
fig.update_yaxes(
    linewidth=1,
    linecolor='dimgray',
    gridcolor='lightgray',
    showspikes=True,
    spikethickness=1,
    spikecolor='dimgray'
)
fig.show()

## Add animation

Add the year the the background

In [ ]:
def background_year(year, xpos=2000, ypos=50):
    """Return the dictionary containing a single position for the text that shows the year"""
    return dict(
        x=[xpos],
        y=[ypos],
        mode='text',
        showlegend=False,
        text=[f'{year}'],
        textposition='middle center',
        textfont=dict(size=200, color='lightgray')
    )

In [ ]:
def gapminder_fig(xaxis='Income', yaxis='Life expectancy'):
    color_map = {
        'Asia': '#ff5872',
        'Americas': '#7feb00',
        'Africa': '#00d5e9',
        'Europe': '#ffe700'
    }
    fig = px.scatter(
        df.query('Year>=2010'),
        x=xaxis,
        y=yaxis,
        color='Region',
        size='Population',
        size_max=60,
        log_x=df_info.loc[xaxis, 'LogScale'],
        log_y=df_info.loc[yaxis, 'LogScale'],
        hover_name='Country',
        hover_data={c: False for c in df.columns},
        color_discrete_map=color_map,
        title='Gapminder<br><sup>Data from gapminder.org, CC-BY license</sup>',
        animation_frame='Year',
        animation_group='Country',
        range_x=[df_info.loc[xaxis, 'Min'], df_info.loc[xaxis, 'Max']],
        range_y=[df_info.loc[yaxis, 'Min'], df_info.loc[yaxis, 'Max']]
    )
    # Adjust markers
    fig.update_traces(marker=dict(line=dict(color='black', width=0.8), opacity=0.9))
    # Adjust figure layout
    fig.update_layout(
        plot_bgcolor='white',
        font=dict(color='dimgray')
    )
    # Adjust axes and grid
    fig.update_xaxes(
        linewidth=1,
        linecolor='dimgray',
        gridcolor='lightgray',
        showspikes=True,
        spikethickness=1,
        spikecolor='dimgray'
    )
    fig.update_yaxes(
        linewidth=1,
        linecolor='dimgray',
        gridcolor='lightgray',
        showspikes=True,
        spikethickness=1,
        spikecolor='dimgray'
    )
    # Show the year in the background
    frame_year = fig.frames[0].name  # Get the year in the first frame
    fig.add_trace(go.Scatter(
        background_year(frame_year, 
                        xpos=df_info.loc[xaxis, 'Mid'],
                        ypos=df_info.loc[yaxis, 'Mid']
                       )
    ))  # Add the scatter plot showing the year to the figure
    fig.data = (fig.data[-1], ) + fig.data[:-1]  # Change the order (put the year at the beginning)
    # Add the year to each of the frames
    for frame in fig.frames:
        frame.data = (
            background_year(
                frame.name,
                xpos=df_info.loc[xaxis, 'Mid'],
                ypos=df_info.loc[yaxis, 'Mid']
            ), 
        ) + frame.data
    fig.update(frames=fig.frames)
    # Add annotations to the axes
    fig.add_annotation(
        x=1, xref='x domain',
        y=0, yref='y domain',
        text=df_info.loc[xaxis, 'Meaning'],
        showarrow=False,
        align='right'
    )
    fig.add_annotation(
        x=0, xref='x domain',
        y=1, yref='y domain',
        text=df_info.loc[yaxis, 'Meaning'],
        showarrow=False,
        valign='top',
        textangle=-90
    )
    # Set the size of the figure (fixed, so it doesn't change with window size)
    fig.update_layout(autosize=False, width=800, height=600)
    return fig
fig = gapminder_fig()
fig.show()

## Use Dash

- Dash html components: https://dash.plotly.com/dash-html-components
- Dash core components: https://dash.plotly.com/dash-core-components

In [ ]:
import dash
from dash import html, dcc
from jupyter_dash import JupyterDash
from dash.dependencies import Input, Output

In [ ]:
attributes = ['Income', 'Life expectancy', 'Fertility', 'Child mortality']

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']
app = JupyterDash(__name__, external_stylesheets=external_stylesheets)

app.layout = html.Div([
    html.H1(
        'Interactive data visualization', 
        style={'fontSize': 50}
    ),
    html.Div([
        html.P('X axis'),
        dcc.Dropdown(
            id='dropdown_x',
            options=[{'label': a, 'value': a} for a in attributes],
            value='Income',
            clearable=False
        )],
        style={'width': '390px', 'display': 'inline-block', 'padding-right': '10px'}
    ),
    html.Div([
        html.P('Y axis'),
        dcc.Dropdown(
            id='dropdown_y',
            options=[{'label': a, 'value': a} for a in attributes],
            value='Life expectancy',
            clearable=False
        )],
        style={'width': '390px', 'display': 'inline-block', 'padding-right': '10px'}
    ),
    dcc.Graph(
        id='plot',
        figure=gapminder_fig()
    )
])

@app.callback(
    Output('plot', 'figure'),
    [Input('dropdown_x', 'value'), Input('dropdown_y', 'value')]
)
def update_plot(value_x, value_y):
    return gapminder_fig(xaxis=value_x, yaxis=value_y)

In [ ]:
app.run_server(debug=True)